In [1]:
import numpy as np
import datetime as dt
import pandas as pd
import os
import warnings
import pickle
from timeit import default_timer as timer
from collections import OrderedDict
from itertools import chain

import matplotlib.pyplot as plt
import plotly.graph_objects as ply_go
import plotly.figure_factory as ply_ff
import plotly.colors as ply_colors 

from scipy import signal
import librosa
import librosa.display as librosa_display

In [2]:
from utils.load_metadata import load_metadata

In [3]:
root = os.getcwd()
directory= '/dataset/subset_dataset/covid19-cough-audio-classification/'
metadata = load_metadata(root, directory, metadata_file="metadata_compiled.csv")

Index(['uuid', 'datetime', 'cough_detected', 'SNR', 'latitude', 'longitude',
       'age', 'gender', 'respiratory_condition', 'fever_muscle_pain', 'status',
       'quality_1', 'cough_type_1', 'dyspnea_1', 'wheezing_1', 'stridor_1',
       'choking_1', 'congestion_1', 'nothing_1', 'diagnosis_1', 'severity_1',
       'quality_2', 'cough_type_2', 'dyspnea_2', 'wheezing_2', 'stridor_2',
       'choking_2', 'congestion_2', 'nothing_2', 'diagnosis_2', 'severity_2',
       'quality_3', 'cough_type_3', 'dyspnea_3', 'wheezing_3', 'stridor_3',
       'choking_3', 'congestion_3', 'nothing_3', 'diagnosis_3', 'severity_3',
       'quality_4', 'cough_type_4', 'dyspnea_4', 'wheezing_4', 'stridor_4',
       'choking_4', 'congestion_4', 'nothing_4', 'diagnosis_4', 'severity_4'],
      dtype='object')
NULL or NA records for each column:
uuid                         0
datetime                     0
cough_detected               0
SNR                          0
latitude                 11466
longitude    

## Dividimos las clases por grupos etarios

In [4]:
metadata['audio_class'] = 'X' # default, we should have none by the end of this classification process
metadata.loc[ (metadata['cough_detected'] >= 0.80) & (metadata['age']>=60) ,'audio_class'] = 'A'
metadata.loc[ (metadata['cough_detected'] >= 0.80) & (metadata['age']>=40) & (metadata['age']<60) ,'audio_class'] = 'B'
metadata.loc[ (metadata['cough_detected'] >= 0.80) & (metadata['age']< 40) ,'audio_class'] = 'C'
metadata.loc[ (metadata['cough_detected'] < 0.80) & (metadata['age']>=60) ,'audio_class'] = 'D'
metadata.loc[ (metadata['cough_detected'] < 0.80) & (metadata['age']>=40) & (metadata['age']<60) ,'audio_class'] = 'E'
metadata.loc[ (metadata['cough_detected'] < 0.80) & (metadata['age']< 40) ,'audio_class'] = 'F'

print("Entries subdivided in classes. Printing the number of entries for each class:")
print(metadata[['audio_class','uuid']].groupby(['audio_class']).count().rename(columns={'uuid':'N_entries'}) )

print("\n\n\nSplitting count by class and status:")
print(metadata[['audio_class','status','uuid']].groupby(['audio_class','status']).count().rename(columns={'uuid':'N_entries'}) )

Entries subdivided in classes. Printing the number of entries for each class:
             N_entries
audio_class           
A                  686
B                 3261
C                 6344
D                  511
E                 1523
F                 2893
X                12332



Splitting count by class and status:
                         N_entries
audio_class status                
A           COVID-19            33
            healthy            600
            symptomatic         53
B           COVID-19           158
            healthy           2561
            symptomatic        542
C           COVID-19           417
            healthy           4744
            symptomatic       1183
D           COVID-19            26
            healthy            431
            symptomatic         54
E           COVID-19           110
            healthy           1193
            symptomatic        220
F           COVID-19           221
            healthy           2203
          

### Parámetros de audio utilizados

In [5]:
my_sampling_rate = int(4096*2)  # Sampling rate, how frequently we want to take a value of the audio curve.
                                 # the max frequency in the STFT will be (approximately) half of this
                               
my_n_fft = 512 # number of frequency bins to be calculated in the STFT; 
               # if my_window_size is None, this drives also the time-sampling window
    
my_n_mfcc = 26 # number of mel-frequencies used for the MFCC calculation. The original article used
               # a number of 13 MFCC frequencies, I am trying to add some extra info   
    
my_window_size = None # should not be greater than n_fft
target_duration = 10 # seconds; shorter audios will be zero padded; longer audios will be cut;
                     # obtained from an earlier dry run over all data and charting the distribution 
                     # of duration of the raw sound samples; 10 sec corresponds to the 97th percentile and 
                     # represent a significant improvement in terms of computing time (x5 faster) 
                     # respect to more conservative choices like 70 seconds (99th percentile)


iclass = "A"   # the class of audio records to be processesed (see previous cells)

### these are the frequency bins used to compute short-term features as per the original article (used as inputs to the cough detection classifier).
### Note that the code here will compute features for all bins but in the original paper they use only non-contiguous values.
### For example, we keep the bin [0, 200] Hz but not the [200, 300] Hz; the lowest bin used inthe rest of htis analysis will be [0, 200] Hz,
### the highest one will be [3800, 3900] Hz
my_psd_freqs = [0.0, 200.0, 300.0, 425, 500.0, 650.0, 950.0, 1150.0, 1400.0, 1800.0, 2300.0, 2400.0, 2850.0, 2950.0, 3800.0, 3900, 4000]
psd_feature_names =['SPEC_CENTROID', 'SPEC_WIDTH', 'SPEC_CREST', 'SPEC_MEAN', 'SPEC_SD', 'SPEC_SKEW']


mfcc_feature_names = [ "MFCC_MEAN_{:02}".format(i) for i in range(0,my_n_mfcc,1)]
mfcc_feature_names = mfcc_feature_names + [ "MFCC_SD_{:02}".format(i) for i in range(0,my_n_mfcc,1)]

In [6]:
tmp_metadata = metadata.loc[metadata['audio_class']==iclass,]

Eliminar entradas donde el SNR es bajo (por lo tanto, el sonido del audio de la tos es de baja calidad)
Este corte debería optimizarse, en esta etapa solo decido eliminar el 10% peor

In [7]:
tmp_metadata = tmp_metadata.loc[tmp_metadata['SNR']>=tmp_metadata['SNR'].quantile(0.10),]

Muestra el conteo de entradas por clase STATUS en el DataFrame completo antes del remuestreo

- Cada grupo tendrá un número de entradas igual al número de registros
- En el grupo más pequeño, redondeado a la decena superior más cercana

In [7]:
from utils.load_metadata import sample_df_balanced, sample_all_data

### Caso 3 clases: COVID-19, Healthy y Symptomatic

In [8]:

# print("Antes del remuestreo, conteo de entradas por clase STATUS en el DataFrame completo:")
# tmp_metadata_count = tmp_metadata[['uuid','status']].groupby(['status']).count()
# print(tmp_metadata_count)
# print(len(tmp_metadata.loc[tmp_metadata['status']=='COVID-19', 'uuid'].unique()))

# # redondeo
# n_resampling = int(np.ceil(tmp_metadata_count['uuid'].min()/10)*10)

# # Realiza un muestreo balanceado del DataFrame usando la función sample_df_balanced
# tmp_metadata = sample_df_balanced(tmp_metadata, 'status', n_resampling)

# print("\nDespués del remuestreo, conteo de entradas por clase STATUS en el DataFrame completo:")
# print(tmp_metadata[['uuid','status']].groupby(['status']).count())
# print(len(tmp_metadata.loc[tmp_metadata['status']=='COVID-19', 'uuid'].unique()))

## Caso 2 clases: COVID-19 y Helathy

In [11]:
# First filter for just COVID-19 and healthy status
filtered_metadata = metadata[metadata['status'].isin(['COVID-19', 'healthy'])]

# Process each class and balance the samples
#balanced_dfs = []
for iclass in ['A', 'B', 'C', 'D', 'E', 'F', 'X']:
    tmp_metadata = filtered_metadata[filtered_metadata['audio_class'] == iclass]
    
    # Skip if class has no samples
    if len(tmp_metadata) == 0:
        continue
        
    # Apply SNR filter
    tmp_metadata = tmp_metadata[tmp_metadata['SNR'] >= tmp_metadata['SNR'].quantile(0.10)]
    
    # Get minimum count and round up to nearest 10
    min_count = tmp_metadata['status'].value_counts().min()
    n_resampling = int(np.ceil(min_count/10)*10)
    
    # Balance the samples
    #balanced_class = sample_all_data(tmp_metadata, 'status', target_size)
    #balanced_dfs.append(balanced_class)

# Combine all balanced classes
final_metadata = pd.concat([tmp_metadata])

# Verify the results
print("\nFinal count by class and status:")
print(final_metadata[['audio_class', 'status', 'uuid']].groupby(['audio_class', 'status']).count())


Final count by class and status:
                      uuid
audio_class status        
X           COVID-19   189
            healthy    745


In [10]:
from utils.preprocessing import prepare_data

In [11]:
data_dir = root + directory

In [12]:
all_data, all_audio_metadata, spectrograms_data = prepare_data(input_data=tmp_metadata, audio_datadir=data_dir, sr=my_sampling_rate, 
                                            target_duration=target_duration, n_fft=my_n_fft, n_mfcc=my_n_mfcc, 
                                            fft_window_size=my_window_size, psd_freq_bins=my_psd_freqs,
                                            mfcc_feature_names=mfcc_feature_names, psd_feature_names=psd_feature_names,
                                            max_audio_samples=None, print_every_n=20, tmp_metadata = tmp_metadata) 

all_audio_metadata = all_audio_metadata.drop_duplicates(subset='UUID', keep='first') # this avoids spurious duplicates at the following merge

print("Merging dataframe with audio features and df with audio metadata")
all_data = pd.merge(all_data,all_audio_metadata,on=['UUID'],how='inner')
all_data.drop(['AUDIO_FILE'],axis=1,inplace=True)

#print(all_data[['UUID','STATUS']].groupby(['STATUS']).count())
print("Shape of full dataframe with features and labels: {}".format(all_data.shape))
all_data.head(10)

Processing file #0: 38593987-2561-42cc-8ee7-731ad1312073.ogg


/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)
/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecat

Processing file #20: 04ccec17-82e0-4393-838d-923e3f6a0ad4.webm


/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)
/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecat

Processing file #40: 0379c586-c500-483c-83a6-95b63afe6931.webm


...

/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)
/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecat

Processing file #100: 3fc24090-97ca-42fd-bb8b-8449c6c86213.ogg


/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)
/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecat


120 files processed in 9.6 seconds

Merging dataframe with audio features and df with audio metadata
Shape of full dataframe with features and labels: (120, 115)


UUID AUDIO_CLASS  COUGH_DETECTED  \
0  38593987-2561-42cc-8ee7-731ad1312073           A          0.9709   
1  42405638-7d4a-447b-a21d-66bf9201ffae           A          0.8497   
2  49f6f0db-97dc-4da4-848e-69bd536b5283           A          1.0000   
3  699446d5-5755-4f69-8b06-2b5adf9e9db0           A          0.9942   
4  28854707-b408-4b25-ace4-0797baff5f85           A          0.9508   
5  9a0f0381-29cd-4a02-8418-633f2a6e09fb           A          0.8790   
6  030f3727-77b6-4696-9078-a4bbef85759f           A          0.9938   
7  e65eb75f-ca15-4027-a0d7-2fea5f957521           A          0.8947   
8  52ffbed1-7126-454b-a06c-6cd8bc4a03c2           A          0.8210   
9  1b427191-6752-40b4-a99b-6f55d44f2a91           A          0.9942   

         SNR   AGE  GENDER  RESPIRATORY_CONDITION  FEVER_MUSCLE_PAIN   STATUS  \
0  17.878600  68.0  female                  False              False  healthy   
1   7.217873  64.0    male                  False              False  healthy   
2   7.738090  68.0    male                  False              False  healthy   
3   9.559821  60.0  female                  False              False  healthy   
4  10.188117  60.0    male                  False              False  healthy   
5  26.317418  68.0  female                  False              False  healthy   
6  19.124473  65.0    male                  False              False  healthy   
7  13.100575  73.0    male                  False              False  healthy   
8  14.203082  65.0  female                  False              False  healthy   
9   9.949858  70.0    male                  False              False  healthy   

   MFCC_MEAN_00  ...  SPEC_SKEW_04  SPEC_SKEW_05  SPEC_SKEW_06  SPEC_SKEW_07  \
0   -362.475188  ...     25.281274     -0.582578     13.939207      3.066893   
1   -391.541735  ...     31.848497    -13.761005     -1.097988    -11.204064   
2   -433.668167  ...     -2.288635     14.876451      7.627362      0.254644   
3   -464.486000  ...    140.559146    -12.910353     10.536465      9.292076   
4   -426.199400  ...     73.980676    -28.830139      1.485041      0.912669   
5   -304.406555  ...     86.989263     10.823841     -2.663351      0.403873   
6   -455.646781  ...    225.394734      0.402172     26.296282     -8.277703   
7   -515.812102  ...     34.451557    -16.245528     -0.519679    -15.698688   
8   -477.598757  ...    109.842076     -1.833811      9.505713     -9.776274   
9   -508.687994  ...     84.830118      1.649945     -2.830557    -10.302261   

        ZCR  SAMPLING_RATE   DURATION  MEAN_SIG   MAX_SIG   MIN_SIG  
0  0.109033           8192   9.984619  0.000002  0.843756 -0.977762  
1  0.122314           8192   9.840088  0.000121  0.980168 -0.879452  
2  0.115479           8192   6.180054  0.000043  0.887938 -0.775076  
3  0.131006           8192   4.920044 -0.000011  0.834167 -0.821553  
4  0.081238           8192   9.840088 -0.000063  0.724170 -0.835692  
5  0.169861           8192  10.013550  0.000012  0.934673 -1.002930  
6  0.100623           8192   6.360107  0.000014  0.788677 -0.746040  
7  0.035059           8192   9.900024 -0.000021  0.637783 -0.812074  
8  0.152478           8192   9.900024 -0.000017  0.609634 -0.551338  
9  0.016895           8192   9.780029  0.000004  0.801635 -0.657418  

[10 rows x 115 columns]

## Salvando la info preprocesada

In [13]:
out_data_filename = root+"/preprocessed_dataset"+"/cough-classification-data_Class{}.pkl".format(iclass)
pd.to_pickle(all_data, out_data_filename)  # save df to file

Revisando que está balanceado

In [14]:
all_data[['UUID','STATUS']].groupby(['STATUS']).count().rename(columns={'UUID':'N_UUID'})

N_UUID
STATUS             
COVID-19         40
healthy          40
symptomatic      40

In [15]:
len(spectrograms_data)

112

In [16]:
spectrograms_data.keys()

dict_keys(['38593987-2561-42cc-8ee7-731ad1312073', '42405638-7d4a-447b-a21d-66bf9201ffae', '49f6f0db-97dc-4da4-848e-69bd536b5283', '699446d5-5755-4f69-8b06-2b5adf9e9db0', '28854707-b408-4b25-ace4-0797baff5f85', '9a0f0381-29cd-4a02-8418-633f2a6e09fb', '030f3727-77b6-4696-9078-a4bbef85759f', 'e65eb75f-ca15-4027-a0d7-2fea5f957521', '52ffbed1-7126-454b-a06c-6cd8bc4a03c2', '1b427191-6752-40b4-a99b-6f55d44f2a91', '32606c74-5d0b-4071-9465-fa221b674669', 'fc176213-aaca-4dc6-9235-d4911a99c6db', '8d9358eb-118e-459f-a9a8-0e5ec3e9636c', '6a295b92-e62b-4e83-823c-1808fb8a3efb', '676f34e4-157b-463d-ba14-6cb5375a3fdb', 'e3157d31-7cc6-4a85-a041-793bbe4cc0ce', 'f8c2bfb9-2333-4366-83d1-c4da5bf12dfe', 'a2232156-6870-4afc-af86-d1d6067e4169', '5f536b76-caa2-4b7e-b403-a963f8267b93', 'd64f6adc-623c-48f7-a6f9-9127cddb20b2', '04ccec17-82e0-4393-838d-923e3f6a0ad4', 'b9b6b300-923b-4780-a294-7da6905d803b', '4759ca9f-1583-4e97-b90e-6b290104e5a9', 'dbcc6cfe-045c-4b9f-b890-23f598a9e6f2', '00e627a2-6da6-452f-bd92-fc8c

In [17]:
spectrograms_data['38593987-2561-42cc-8ee7-731ad1312073'].keys()

dict_keys(['stft', 'mfcc', 'metadata', 'features'])

In [18]:
spectrograms_data['38593987-2561-42cc-8ee7-731ad1312073']['metadata']

{'uuid': '38593987-2561-42cc-8ee7-731ad1312073',
 'filename': '38593987-2561-42cc-8ee7-731ad1312073.ogg',
 'duration': 10,
 'sr': 8192,
 'n_fft': 512}

In [19]:
spectrograms_data['38593987-2561-42cc-8ee7-731ad1312073']['features']

OrderedDict([('UUID', '38593987-2561-42cc-8ee7-731ad1312073'),
             ('AUDIO_CLASS', 'A'),
             ('COUGH_DETECTED', 0.9709),
             ('SNR', 17.87860036),
             ('AGE', 68.0),
             ('GENDER', 'female'),
             ('RESPIRATORY_CONDITION', False),
             ('FEVER_MUSCLE_PAIN', False),
             ('STATUS', 'healthy'),
             ('MFCC_MEAN_00', np.float64(-362.47518773085034)),
             ('MFCC_MEAN_01', np.float64(47.22392741434315)),
             ('MFCC_MEAN_02', np.float64(-8.003680601646353)),
             ('MFCC_MEAN_03', np.float64(-6.6875113261522285)),
             ('MFCC_MEAN_04', np.float64(-20.408123794702618)),
             ('MFCC_MEAN_05', np.float64(-18.005045372308203)),
             ('MFCC_MEAN_06', np.float64(-11.250143975076536)),
             ('MFCC_MEAN_07', np.float64(-10.387181977234768)),
             ('MFCC_MEAN_08', np.float64(-13.459098031324372)),
             ('MFCC_MEAN_09', np.float64(-10.274272357630277)),


In [20]:
len(spectrograms_data['38593987-2561-42cc-8ee7-731ad1312073']['features'])

110

In [21]:
for key in spectrograms_data.keys():
    print(spectrograms_data[key]['features']['STATUS'])

healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
healthy
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
COVID-19
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptomatic
symptoma

In [22]:
out_data_filename = root+"/preprocessed_dataset"+"/cough-classification-data_Class{}_spectrograms.pkl".format(iclass)
pd.to_pickle(spectrograms_data, out_data_filename)  

## Entrenando un modelo

In [23]:
import numpy as np
import tensorflow as tf
from tensorflow.keras import layers, models
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
import json

def prepare_training_data(spectrograms_data):
    """
    Prepara los datos para el entrenamiento del modelo CNN.
    """
    # Extraer MFCCs y etiquetas
    X = []
    y = []
    
    for uuid in spectrograms_data.keys():
        mfcc = np.array(spectrograms_data[uuid]['mfcc']['coefficients'])
        status = spectrograms_data[uuid]['features']['STATUS']
        
        # Añadir dimensión de canal
        mfcc = np.expand_dims(mfcc, axis=-1)
        
        X.append(mfcc)
        y.append(status)
    
    X = np.array(X)
    y = np.array(y)
    
    # Codificar etiquetas
    label_encoder = LabelEncoder()
    y_encoded = label_encoder.fit_transform(y)
    y_onehot = tf.keras.utils.to_categorical(y_encoded)
    
    return X, y_onehot, label_encoder

def create_cnn_model(input_shape, num_classes):
    """
    Crea un modelo CNN para clasificación de audio.
    """
    model = models.Sequential([
        # Primera capa convolucional
        layers.Conv2D(32, (3, 3), activation='relu', padding='same', input_shape=input_shape),
        layers.BatchNormalization(),
        layers.MaxPooling2D((2, 2)),
        layers.Dropout(0.25),
        
        # Segunda capa convolucional
        layers.Conv2D(64, (3, 3), activation='relu', padding='same'),
        layers.BatchNormalization(),
        layers.MaxPooling2D((2, 2)),
        layers.Dropout(0.25),
        
        # Tercera capa convolucional
        layers.Conv2D(128, (3, 3), activation='relu', padding='same'),
        layers.BatchNormalization(),
        layers.MaxPooling2D((2, 2)),
        layers.Dropout(0.25),
        
        # Cuarta capa convolucional
        layers.Conv2D(256, (3, 3), activation='relu', padding='same'),
        layers.BatchNormalization(),
        layers.MaxPooling2D((2, 2)),
        layers.Dropout(0.25),
        
        # Capas densas
        layers.Flatten(),
        layers.Dense(512, activation='relu'),
        layers.BatchNormalization(),
        layers.Dropout(0.5),
        layers.Dense(num_classes, activation='softmax')
    ])
    
    return model

def train_model(X, y, label_encoder, batch_size=32, epochs=50):
    """
    Entrena el modelo CNN.
    """
    # Dividir datos en train/validation/test
    X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.3, random_state=42)
    X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.5, random_state=42)
    
    # Crear y compilar modelo
    input_shape = X_train.shape[1:]
    num_classes = y_train.shape[1]
    
    model = create_cnn_model(input_shape, num_classes)
    
    # Compilar modelo
    model.compile(
        optimizer='adam',
        loss='categorical_crossentropy',
        metrics=['accuracy']
    )
    
    # Callbacks
    early_stopping = tf.keras.callbacks.EarlyStopping(
        monitor='val_loss',
        patience=10,
        restore_best_weights=True
    )
    
    reduce_lr = tf.keras.callbacks.ReduceLROnPlateau(
        monitor='val_loss',
        factor=0.2,
        patience=5,
        min_lr=1e-6
    )
    
    # Entrenar modelo
    history = model.fit(
        X_train,
        y_train,
        batch_size=batch_size,
        epochs=epochs,
        validation_data=(X_val, y_val),
        callbacks=[early_stopping, reduce_lr]
    )
    
    # Evaluar modelo
    test_loss, test_acc = model.evaluate(X_test, y_test)
    print(f"\nTest accuracy: {test_acc:.4f}")
    
    # Predicciones en conjunto de prueba
    y_pred = model.predict(X_test)
    y_pred_classes = np.argmax(y_pred, axis=1)
    y_test_classes = np.argmax(y_test, axis=1)
    
    # Imprimir reporte de clasificación
    from sklearn.metrics import classification_report
    class_names = label_encoder.classes_
    print("\nClassification Report:")
    print(classification_report(
        y_test_classes,
        y_pred_classes,
        target_names=class_names
    ))
    
    return model, history, (X_test, y_test)

In [24]:
# Preparar datos
X, y, label_encoder = prepare_training_data(spectrograms_data)

# Entrenar modelo
model, history, test_data = train_model(
X,
y,
label_encoder,
batch_size=32,
epochs=50
)

Epoch 1/50


/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/keras/src/layers/convolutional/base_conv.py:107: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


3/3 ━━━━━━━━━━━━━━━━━━━━ 2s 127ms/step - accuracy: 0.3296 - loss: 2.1952 - val_accuracy: 0.4706 - val_loss: 2.1328 - learning_rate: 0.0010
Epoch 2/50
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 60ms/step - accuracy: 0.4481 - loss: 1.3732 - val_accuracy: 0.5294 - val_loss: 2.3018 - learning_rate: 0.0010
Epoch 3/50
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 59ms/step - accuracy: 0.4688 - loss: 1.4466 - val_accuracy: 0.5294 - val_loss: 3.6734 - learning_rate: 0.0010
Epoch 4/50
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 60ms/step - accuracy: 0.4741 - loss: 1.4065 - val_accuracy: 0.5294 - val_loss: 5.4348 - learning_rate: 0.0010
Epoch 5/50
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 59ms/step - accuracy: 0.5139 - loss: 1.2760 - val_accuracy: 0.5294 - val_loss: 6.4705 - learning_rate: 0.0010
Epoch 6/50
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 59ms/step - accuracy: 0.5736 - loss: 1.3021 - val_accuracy: 0.5294 - val_loss: 5.0981 - learning_rate: 0.0010
Epoch 7/50
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 60ms/step - accuracy: 0.6565 - loss: 0.9551 - val_accuracy: 0.5294 - val_loss

/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set 

In [25]:
# Guardar modelo
model.save(root+'/models/'+'model_0.keras')

## Entrenando con más datos!

In [26]:
# Filtrar solo las clases A, B y C
metadata_filtered = metadata[metadata['audio_class'].isin(['A', 'B', 'C'])].copy()
tmp_metadata_filtered = metadata_filtered.loc[metadata_filtered['SNR']>=metadata_filtered['SNR'].quantile(0.10),]

# CONTANDO
print("Antes del remuestreo, conteo de entradas por clase STATUS en el DataFrame completo:")
tmp_metadata_count = tmp_metadata_filtered[['uuid','status']].groupby(['status']).count()
print(tmp_metadata_count)
print(len(tmp_metadata_filtered.loc[tmp_metadata_filtered['status']=='COVID-19', 'uuid'].unique()))

# redondeo
# n_resampling = int(np.ceil(tmp_metadata_count['uuid'].min()/10)*10)

# Realiza un muestreo balanceado del DataFrame usando la función sample_df_balanced
# tmp_metadata_filtered = sample_df_balanced(tmp_metadata_filtered, 'status', n_resampling)

print("\nDespués del remuestreo, conteo de entradas por clase STATUS en el DataFrame completo:")
print(tmp_metadata_filtered[['uuid','status']].groupby(['status']).count())
print(len(tmp_metadata_filtered.loc[tmp_metadata_filtered['status']=='COVID-19', 'uuid'].unique()))


### TRASNFORMANDO
all_data_abc, all_audio_metadata_abc, spectrograms_data_abc = prepare_data(input_data=tmp_metadata_filtered, audio_datadir=data_dir, sr=my_sampling_rate, 
                                            target_duration=target_duration, n_fft=my_n_fft, n_mfcc=my_n_mfcc, 
                                            fft_window_size=my_window_size, psd_freq_bins=my_psd_freqs,
                                            mfcc_feature_names=mfcc_feature_names, psd_feature_names=psd_feature_names,
                                            max_audio_samples=None, print_every_n=20, tmp_metadata = tmp_metadata_filtered) 

all_audio_metadata_abc = all_audio_metadata_abc.drop_duplicates(subset='UUID', keep='first') # this avoids spurious duplicates at the following merge

print("Merging dataframe with audio features and df with audio metadata")
all_data_abc = pd.merge(all_data_abc,all_audio_metadata_abc,on=['UUID'],how='inner')
all_data_abc.drop(['AUDIO_FILE'],axis=1,inplace=True)

#print(all_data[['UUID','STATUS']].groupby(['STATUS']).count())
print("Shape of full dataframe with features and labels: {}".format(all_data_abc.shape))
all_data_abc.head(10)


out_data_filename = root+"/preprocessed_dataset"+"/cough-classification-data_Class{}_spectrograms_abc.pkl".format(iclass)
pd.to_pickle(spectrograms_data_abc, out_data_filename)  

Antes del remuestreo, conteo de entradas por clase STATUS en el DataFrame completo:
             uuid
status           
COVID-19      529
healthy      7104
symptomatic  1629
529

Después del remuestreo, conteo de entradas por clase STATUS en el DataFrame completo:
             uuid
status           
COVID-19      529
healthy      7104
symptomatic  1629
529
Processing file #0: 00039425-7f3a-42aa-ac13-834aaa2b6b92.webm


/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)
/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecat

Processing file #20: 00802ac6-0e3b-4bba-bcdc-014f1fde7432.webm


/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)
/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecat

Processing file #40: 012a8047-9ccb-43eb-8cf6-349ac093801a.webm


...

Processing file #9240: ff4ea768-cb72-4bb8-b546-978439dd005c.webm


/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)
/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecat

Processing file #9260: ffedc843-bfc2-4ad6-a749-2bc86bdac84a.webm


/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)
/Users/rodolfolobocarrasco/Documents/projects/ESPOL-PROJECT/ESPOL-coughvid-project/utils/preprocessing.py:12: UserWarning: PySoundFile failed. Trying audioread instead.
  t, sr = librosa.load(indir + filename, sr=sr, mono=True)
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/librosa/core/audio.py:184: FutureWarning: librosa.core.audio.__audioread_load
	Deprecat


9262 files processed in 1111.2 seconds

Merging dataframe with audio features and df with audio metadata
Shape of full dataframe with features and labels: (9262, 115)


In [28]:
# Preparar datos
X, y, label_encoder = prepare_training_data(spectrograms_data)

# Entrenar modelo
model, history, test_data = train_model(
X,
y,
label_encoder,
batch_size=32,
epochs=50
)

Epoch 1/50


/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/keras/src/layers/convolutional/base_conv.py:107: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


3/3 ━━━━━━━━━━━━━━━━━━━━ 2s 134ms/step - accuracy: 0.3993 - loss: 1.8112 - val_accuracy: 0.2353 - val_loss: 4.1235 - learning_rate: 0.0010
Epoch 2/50
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 64ms/step - accuracy: 0.4445 - loss: 1.5551 - val_accuracy: 0.2353 - val_loss: 5.8986 - learning_rate: 0.0010
Epoch 3/50
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 66ms/step - accuracy: 0.4833 - loss: 1.5443 - val_accuracy: 0.2941 - val_loss: 3.7533 - learning_rate: 0.0010
Epoch 4/50
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 64ms/step - accuracy: 0.5931 - loss: 1.3336 - val_accuracy: 0.4118 - val_loss: 4.5447 - learning_rate: 0.0010
Epoch 5/50
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 66ms/step - accuracy: 0.6124 - loss: 1.2179 - val_accuracy: 0.4706 - val_loss: 4.8912 - learning_rate: 0.0010
Epoch 6/50
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 77ms/step - accuracy: 0.5580 - loss: 1.2760 - val_accuracy: 0.2353 - val_loss: 11.1296 - learning_rate: 0.0010
Epoch 7/50
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 64ms/step - accuracy: 0.5722 - loss: 1.2428 - val_accuracy: 0.2353 - val_los

/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/Users/rodolfolobocarrasco/Library/Caches/pypoetry/virtualenvs/clear-J92jq7Lm-py3.11/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set 